In [1]:
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
from urllib.request import urlopen
import json

In [2]:
state_GDP = pd.read_csv("SAGDP1__ALL_AREAS_1997_2022.csv", skipfooter=4, engine='python')
state_GDP['GeoFIPS'] = state_GDP['GeoFIPS'].map(lambda x: x.lstrip(' "').rstrip('0"'))
state_GDP['GeoFIPS'] = state_GDP['GeoFIPS'].apply(lambda x: x + '0' if len(x) == 1 else x)
state_GDP = state_GDP[state_GDP['LineCode'] == 1]
state_GDP = state_GDP.drop(['Region', 'TableName', 'TableName', 'LineCode','IndustryClassification', 'Description', 'Unit'], axis=1)
state_GDP.head()

GeoFIPS        GeoName        1997        1998        1999        2000  \
0           United States  11529157.0  12045824.0  12623361.0  13138035.0   
8       01        Alabama    144501.2    149568.2    154900.2    157221.3   
16      02         Alaska     42211.3     41095.9     40590.5     39406.6   
24      04        Arizona    168408.8    183060.5    198699.9    208439.5   
32      05       Arkansas     82571.3     84570.8     89115.2     89871.7   

          2001        2002        2003        2004  ...        2013  \
0   13263417.0  13488357.0  13865519.0  14399696.0  ...  16553348.0   
8     156853.2    160422.4    165134.7    176625.0  ...    191369.8   
16     40958.7     42979.0     42355.3     44055.0  ...     55354.3   
24    213166.2    220696.7    234065.9    244317.3  ...    273481.9   
32     89789.0     92950.5     96944.5    101733.6  ...    110752.4   

          2014        2015        2016        2017        2018        2019  \
0   16932051.0  17390295.0  17680274.0  18076651.0  18609078.0  19036052.0   
8     189886.3    191335.2    194283.8    196974.9    200372.6    203432.7   
16     54188.2     54740.8     54246.6     54278.7     53327.0     53433.8   
24    276948.9    282577.0    291275.2    303606.1    314827.5    325395.3   
32    111734.5    112351.0    112798.1    113850.2    115885.2    117126.2   

          2020        2021        2022  
0   18509143.0  19609812.0  20014128.0  
8     199880.8    209979.3    213264.8  
16     50705.2     50869.4     49633.7  
24    327178.0    347656.0    356417.0  
32    117268.2    123347.3    126532.2  

[5 rows x 28 columns]

In [3]:
# Create a new dataframe with 'GeoFIPS', 'GeoName', 'year', and 'GDP' columns
state_GDP_melted = pd.melt(state_GDP, id_vars=['GeoFIPS', 'GeoName'], var_name='year', value_name='GDP')

# Convert 'year' column from string to int
state_GDP_melted['year'] = state_GDP_melted['year'].astype(int)

# Sort the dataframe by 'GeoFIPS' and 'year'
state_GDP_melted = state_GDP_melted.sort_values(['GeoFIPS', 'year'])

# Reset the index
state_GDP_melted = state_GDP_melted.reset_index(drop=True)
state_GDP_melted

GeoFIPS        GeoName  year         GDP
0             United States  1997  11529157.0
1             United States  1998  12045824.0
2             United States  1999  12623361.0
3             United States  2000  13138035.0
4             United States  2001  13263417.0
...      ...            ...   ...         ...
1555      98       Far West  2018   3658195.2
1556      98       Far West  2019   3772219.3
1557      98       Far West  2020   3689413.4
1558      98       Far West  2021   3963354.0
1559      98       Far West  2022   3993761.8

[1560 rows x 4 columns]

In [4]:
state_GDP_melted.dtypes

GeoFIPS    object
GeoName    object
year        int64
GDP        object
dtype: object

In [5]:
# Create a new dataframe with the relevant columns
state_GDP_melted['GDP'] = pd.to_numeric(state_GDP_melted['GDP'], errors='coerce')
state_gdp_growth = state_GDP_melted[['GeoFIPS','GeoName', 'year', 'GDP']].copy()

# Calculate the GDP growth rate for each state
state_gdp_growth['GDP_growth_rate'] = state_gdp_growth.groupby('GeoFIPS')['GDP'].pct_change()

# Remove the first year (1997) for each state
state_gdp_growth = state_gdp_growth[state_gdp_growth['year'] > 1997]

# Reset the index
state_gdp_growth.reset_index(drop=True, inplace=True)

# Print the dataframe
state_gdp_growth

GeoFIPS        GeoName  year         GDP  GDP_growth_rate
0             United States  1998  12045824.0         0.044814
1             United States  1999  12623361.0         0.047945
2             United States  2000  13138035.0         0.040772
3             United States  2001  13263417.0         0.009543
4             United States  2002  13488357.0         0.016959
...      ...            ...   ...         ...              ...
1495      98       Far West  2018   3658195.2         0.043746
1496      98       Far West  2019   3772219.3         0.031169
1497      98       Far West  2020   3689413.4        -0.021952
1498      98       Far West  2021   3963354.0         0.074250
1499      98       Far West  2022   3993761.8         0.007672

[1500 rows x 5 columns]

In [6]:
state_gdp_growth_only = state_gdp_growth.loc[state_gdp_growth['GeoName'] != 'United States']
state_gdp_growth_only = state_gdp_growth_only[ (state_gdp_growth_only['GeoFIPS'].astype(int) <= 56)]
# Convert FIPS to string
state_gdp_growth_only['year'] = state_gdp_growth_only['year'].astype(int)
state_gdp_growth_only

GeoFIPS  GeoName  year       GDP  GDP_growth_rate
25        01  Alabama  1998  149568.2         0.035065
26        01  Alabama  1999  154900.2         0.035649
27        01  Alabama  2000  157221.3         0.014984
28        01  Alabama  2001  156853.2        -0.002341
29        01  Alabama  2002  160422.4         0.022755
...      ...      ...   ...       ...              ...
1295      56  Wyoming  2018   38080.1         0.014885
1296      56  Wyoming  2019   38446.6         0.009624
1297      56  Wyoming  2020   36268.6        -0.056650
1298      56  Wyoming  2021   36400.0         0.003623
1299      56  Wyoming  2022   36346.1        -0.001481

[1275 rows x 5 columns]

In [7]:
state_gdp_growth_only.dtypes

GeoFIPS             object
GeoName             object
year                 int64
GDP                float64
GDP_growth_rate    float64
dtype: object

In [8]:
print(state_gdp_growth_only.shape)
print(state_gdp_growth_only.dtypes)
print(state_gdp_growth_only.head())

(1275, 5)
GeoFIPS             object
GeoName             object
year                 int64
GDP                float64
GDP_growth_rate    float64
dtype: object
   GeoFIPS  GeoName  year       GDP  GDP_growth_rate
25      01  Alabama  1998  149568.2         0.035065
26      01  Alabama  1999  154900.2         0.035649
27      01  Alabama  2000  157221.3         0.014984
28      01  Alabama  2001  156853.2        -0.002341
29      01  Alabama  2002  160422.4         0.022755


In [16]:
# Load the GeoJSON file for US states
with urlopen('https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json') as response:
    us_states_geojson = json.load(response)
    
# Create the map with a slider
#fig_states = go.Figure()

# Create the traces for GDP and GDP growth rate
gdp_trace = px.choropleth_mapbox(
    state_gdp_growth_only,
    geojson=us_states_geojson,
    locations='GeoFIPS',
    color='GDP',
    color_continuous_scale='Viridis',
    animation_frame='year',
    hover_name='GeoName',
    hover_data=['GDP'],
    range_color=(state_gdp_growth_only['GDP'].min(), state_gdp_growth_only['GDP'].max()),
    mapbox_style="carto-positron",
    zoom=3, center={"lat": 37.0902, "lon": -95.7129},
    opacity=0.5,
)

# Update the layout
gdp_trace.update_layout(
    title=dict(x=0.5, xanchor="center"),
    margin={"r": 0, "t": 40, "l": 0, "b": 0},
    coloraxis_colorbar=dict(title="US States GDP (1998-2022)"),
)

gdp_trace.show()

In [17]:
import plotly.offline as pyo

pyo.plot(gdp_trace, filename='GDP_by_state.html', auto_open=True)

'GDP_by_state.html'

In [18]:
gdp_growth_trace = px.choropleth_mapbox(
    state_gdp_growth_only,
    geojson=us_states_geojson,
    locations='GeoFIPS',
    color='GDP_growth_rate',
    color_continuous_scale='Viridis',
    animation_frame='year',
    hover_name='GeoName',
    hover_data=['GDP_growth_rate'],
    range_color=(state_gdp_growth_only['GDP_growth_rate'].min(), state_gdp_growth_only['GDP_growth_rate'].max()),
    mapbox_style="carto-positron",
    zoom=3, center={"lat": 37.0902, "lon": -95.7129},
    opacity=0.5,
)

# Update the layout
gdp_growth_trace.update_layout(
    title=dict(x=0.5, xanchor="center"),
    margin={"r": 0, "t": 40, "l": 0, "b": 0},
    coloraxis_colorbar=dict(title="US States GDP Growth Rate (1998-2022)"),
)

gdp_growth_trace.show()

In [19]:
import plotly.offline as pyo

pyo.plot(gdp_growth_trace, filename='GDP_Growth_Rate_by_state.html', auto_open=True)

'GDP_Growth_Rate_by_state.html'

In [23]:
# Calculate the US average GDP growth rate for each year
us_average_gdp_growth = state_gdp_growth_only.groupby('year')['GDP_growth_rate'].mean().reset_index()
us_average_gdp_growth['GeoName'] = 'US Average'

# Append the US average GDP growth rate to the state GDP growth rate DataFrame
all_gdp_growth = pd.concat([state_gdp_growth_only, us_average_gdp_growth], ignore_index=True)

# Create the line chart
fig = go.Figure()

# Add a trace for each state and the US average
for state in all_gdp_growth['GeoName'].unique():
    state_data = all_gdp_growth[all_gdp_growth['GeoName'] == state]
    fig.add_trace(
        go.Scatter(
            x=state_data['year'],
            y=state_data['GDP_growth_rate'],
            name=state,
            visible=False
        )
    )

# Make the US average trace visible by default
fig.data[1].visible = True

# Create a list of buttons for the dropdown menu
buttons = [dict(
    label=state,
    method='update',
    args=[{'visible': [s == state for s in all_gdp_growth['GeoName'].unique()]},
          {'title': f'GDP Growth Rate: {state}'}])
    for state in all_gdp_growth['GeoName'].unique()]

# Add the dropdown menu to the layout
fig.update_layout(
    updatemenus=[
        dict(
            type='dropdown',
            showactive=True,
            buttons=buttons,
            direction="down",
            pad={"r": 10, "t": 10},
            x=1.1,
            xanchor="left",
            y=1.1,
            yanchor="top"
        )
    ]
)

# Update the layout
fig.update_layout(
    title=dict(text="GDP Growth Rate: US Average", x=0.5, xanchor="center"),
    xaxis_title="Year",
    yaxis_title="GDP Growth Rate",
)

# Show the plot
fig.show()

In [37]:
# Calculate the US average GDP growth rate for each year
us_average_gdp_growth = state_gdp_growth_only.groupby('year')['GDP_growth_rate'].mean().reset_index()
us_average_gdp_growth['GeoName'] = 'US Average'

# Append the US average GDP growth rate to the state GDP growth rate DataFrame
all_gdp_growth = pd.concat([state_gdp_growth_only, us_average_gdp_growth], ignore_index=True)

# Create the line chart
fig = go.Figure()

# Add a trace for each state and the US average
for state in all_gdp_growth['GeoName'].unique():
    state_data = all_gdp_growth[all_gdp_growth['GeoName'] == state]
    fig.add_trace(
        go.Scatter(
            x=state_data['year'],
            y=state_data['GDP_growth_rate'],
            name=state,
            visible=False
        )
    )

# Make the US average trace visible by default
fig.data[-1].visible = True

# Create buttons for the first dropdown menu (Selection)
buttons1 = [dict(
    label=state,
    method='update',
    args=[{'visible': [s == state for s in all_gdp_growth['GeoName'].unique()]},
          {'title': f'GDP Growth Rate: {state}'}])
    for state in all_gdp_growth['GeoName'].unique()]

# Create buttons for the second dropdown menu (Comparison)
def create_button2(state):
    idx = all_gdp_growth['GeoName'].unique().tolist().index(state)
    new_visible = [fig.data[i].visible for i in range(len(fig.data))]
    new_visible[idx] = not new_visible[idx]
    return dict(label=state, method='update', args=[{'visible': new_visible}, {}])

buttons2 = [create_button2(state) for state in all_gdp_growth['GeoName'].unique()]

# Add the dropdown menus to the layout
fig.update_layout(
    updatemenus=[
        dict(
            type='dropdown',
            showactive=True,
            buttons=buttons1,
            direction="down",
            pad={"r": 10, "t": 10},
            x=1.2,
            xanchor="left",
            y=1.1,
            yanchor="top",
            bgcolor="lightgrey",
        ),
        dict(
            type='dropdown',
            showactive=True,
            buttons=buttons2,
            direction="down",
            pad={"r": 10, "t": 10},
            x=1.2,
            xanchor="left",
            y=0.8,
            yanchor="top",
            bgcolor="lightgrey",
        )
    ],
    annotations=[
        dict(
            x=1.3,
            y=1.13,
            xref="paper",
            yref="paper",
            text="Selection:",
            showarrow=False,
            font=dict(size=14)
        ),
        dict(
            x=1.3,
            y=0.85,
            xref="paper",
            yref="paper",
            text="Comparison:",
            showarrow=False,
            font=dict(size=14)
        )
    ]
)
# Update the layout
fig.update_layout(
    title=dict(text="GDP Growth Rate: US Average", x=0.5, xanchor="center"),
    xaxis_title="Year",
    yaxis_title="GDP Growth Rate",
)

# Show the plot
fig.show()

In [38]:
import plotly.offline as pyo

pyo.plot(fig, filename='GDP_Growth_Rate_state_Linegraph.html', auto_open=True)

'GDP_Growth_Rate_state_Linegraph.html'